In [ ]:
!pip install -U kaleido

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 79.9/79.9 MB 7.9 MB/s eta 0:00:00


In [ ]:
import pandas as pd
import json
import plotly.express as px
import plotly.graph_objects as go
from bs4 import BeautifulSoup
from urllib.request import Request, urlopen
import plotly.io as pio

In [ ]:
url_colectivos = urlopen("https://cdn.buenosaires.gob.ar/datosabiertos/datasets/transporte-y-obras-publicas/colectivos-recorridos/recorrido-colectivos.geojson")

In [ ]:
def coordinate_extract(colectivos, empty_list):
    for feature in colectivos['features']:
      if feature['geometry']['type'] == 'MultiLineString':
        for line in feature['geometry']['coordinates']:
          empty_list.extend(line)
          empty_list.append([None, None])
      if feature['geometry']['type'] == "MultiPolygon":
        for polyg in feature['geometry']['coordinates']:
          empty_list.extend(polyg[0])
          empty_list.append([None, None])
      if feature["geometry"]["type"] == "Point":
        empty_list.extend([feature['geometry']['coordinates']])
        empty_list.append([None, None])

In [ ]:
colectivos = json.load(url_colectivos)

colectivos_coords = []

coordinate_extract(colectivos, colectivos_coords)

colectivos_lons, colectivos_lats = zip(*colectivos_coords)

In [ ]:
colectivos_CABA = go.Scattergeo(
    lat=colectivos_lats,
    lon=colectivos_lons,
    mode='lines+text',
    line=dict(color='black', width=1),
    opacity=0.5,
    showlegend=False,
    hoverinfo='skip'
)

In [ ]:
url_paradas = urlopen('https://cdn.buenosaires.gob.ar/datosabiertos/datasets/transporte-y-obras-publicas/colectivos-paradas/paradas-de-colectivo.geojson')

In [ ]:
paradas = json.load(url_paradas)

paradas_coords = []

coordinate_extract(paradas, paradas_coords)

paradas_lons, paradas_lats = zip(*paradas_coords)

In [ ]:
paradas_CABA = go.Scattergeo(
    lat=paradas_lats,
    lon=paradas_lons,
    mode='markers',
    marker=dict(color='rgba(27, 158, 119, 1)', size=3),
    opacity=1,
    showlegend=False,
    hoverinfo='skip'
)

In [ ]:
def maps_layout_and_annotation(fig):
  fig.update_layout(
      paper_bgcolor='rgba(255,255,255,1)',
      margin=dict(
          t = 150,
          b = 0,
          l = 0,
          r = 0
      ),
      height = 900,
      width = 900,
      title = dict(
        text = "<b>Recorrido de colectivos en Buenos Aires</b><br><sup>Red de transporte público: colectivos.<br><sup><b>Fuente</b>: BA Data.</sup></sup>",
        xanchor = 'left',
        x = 0.0325,
        yanchor = 'top',
        y = 0.95,
        font = dict(
            size = 26,
            family="Courier New",
            color = 'black'
        )
        ),
      geo = dict(
        center = dict(
            lat = -34.616,
            lon = -58.435
        ),
        bgcolor = 'rgba(255,255,255,1)',
        projection_type = 'mercator',
        projection_scale = 1640,
        resolution = 50,
        showlakes = False,
        showcoastlines = False,
        showland = False,
        showocean = False,
        showframe = False,
        showcountries = False,
    )
  )

In [ ]:
mapa_colectivos = go.Figure()

In [ ]:
mapa_colectivos.add_trace(colectivos_CABA)

mapa_colectivos.add_trace(paradas_CABA)

maps_layout_and_annotation(mapa_colectivos)

In [ ]:
mapa_colectivos

In [ ]:
pio.write_html(mapa_colectivos,
               file='mapa_colectivos.html',
               full_html=True)